**Copyright 2021 The TensorFlow Authors.**

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://www.tensorflow.org/model_optimization/guide/combine/cqat_example"><img src="https://www.tensorflow.org/images/tf_logo_32px.png" />View on TensorFlow.org</a>
  </td>
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/tensorflow/model-optimization/blob/master/tensorflow_model_optimization/g3doc/guide/combine/cqat_example.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/tensorflow/model-optimization/blob/master/tensorflow_model_optimization/g3doc/guide/combine/cqat_example.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View on GitHub</a>
  </td>
  <td>
    <a href="https://storage.googleapis.com/tensorflow_docs/model-optimization/tensorflow_model_optimization/g3doc/guide/combine/cqat_example.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png" />Download notebook</a>
  </td>
</table>

# Cluster preserving quantization aware training (CQAT) Keras example

## Overview

This is an end to end example showing the usage of the **cluster preserving quantization aware training (CQAT)** API, part of the TensorFlow Model Optimization Toolkit's collaborative optimization pipeline.

### Other pages

For an introduction to the pipeline and other available techniques, see the [collaborative optimization overview page](https://www.tensorflow.org/model_optimization/guide/combine/collaborative_optimization).

### Contents

In the tutorial, you will:

1. Train a `keras` model for the MNIST dataset from scratch.
2. Fine-tune the model with clustering and see the accuracy.
3. Apply QAT and observe the loss of clusters.
4. Apply CQAT and observe that the clustering applied earlier has been preserved.
5. Generate a TFLite model and observe the effects of applying CQAT on it.
6. Compare the achieved CQAT model accuracy with a model quantized using post-training quantization.

## Setup

You can run this Jupyter Notebook in your local [virtualenv](https://www.tensorflow.org/install/pip?lang=python3#2.-create-a-virtual-environment-recommended) or [colab](https://colab.sandbox.google.com/). For details of setting up dependencies, please refer to the [installation guide](https://www.tensorflow.org/model_optimization/guide/install). 

In [2]:
! pip install -q tensorflow-model-optimization

In [3]:
import tensorflow as tf
import tf_keras as keras

import numpy as np
import tempfile
import zipfile
import os

2025-06-21 11:41:18.910447: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1750506078.934254   35128 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1750506078.941543   35128 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1750506078.959971   35128 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1750506078.959996   35128 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1750506078.959999   35128 computation_placer.cc:177] computation placer alr

## Train a keras model for MNIST without clustering

In [4]:
# Load MNIST dataset
mnist = keras.datasets.mnist
(train_images, train_labels), (test_images, test_labels) = mnist.load_data()

# Normalize the input image so that each pixel value is between 0 to 1.
train_images = train_images / 255.0
test_images  = test_images / 255.0

model = keras.Sequential([
  keras.layers.InputLayer(input_shape=(28, 28)),
  keras.layers.Reshape(target_shape=(28, 28, 1)),
  keras.layers.Conv2D(filters=12, kernel_size=(3, 3),
                         activation=tf.nn.relu),
  keras.layers.MaxPooling2D(pool_size=(2, 2)),
  keras.layers.Flatten(),
  keras.layers.Dense(10)
])

# Train the digit classification model
model.compile(optimizer='adam',
              loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

model.fit(
    train_images,
    train_labels,
    validation_split=0.1,
    epochs=10
)

2025-06-21 11:41:22.863055: E external/local_xla/xla/stream_executor/cuda/cuda_platform.cc:51] failed call to cuInit: INTERNAL: CUDA error: Failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected


Epoch 1/10


   1/1688 [..............................] - ETA: 13:27 - loss: 2.2823 - accuracy: 0.1875

  11/1688 [..............................] - ETA: 8s - loss: 2.1784 - accuracy: 0.2386   

  22/1688 [..............................] - ETA: 8s - loss: 2.0450 - accuracy: 0.3722

...

1645/1688 [============================>.] - ETA: 0s - loss: 0.0372 - accuracy: 0.9890

1657/1688 [============================>.] - ETA: 0s - loss: 0.0372 - accuracy: 0.9890

1669/1688 [============================>.] - ETA: 0s - loss: 0.0372 - accuracy: 0.9890

1681/1688 [============================>.] - ETA: 0s - loss: 0.0373 - accuracy: 0.9889

1688/1688 [==============================] - 7s 4ms/step - loss: 0.0373 - accuracy: 0.9889 - val_loss: 0.0629 - val_accuracy: 0.9825


### Evaluate the baseline model and save it for later usage

In [5]:
_, baseline_model_accuracy = model.evaluate(
    test_images, test_labels, verbose=0)

print('Baseline test accuracy:', baseline_model_accuracy)

_, keras_file = tempfile.mkstemp('.h5')
print('Saving model to: ', keras_file)
keras.models.save_model(model, keras_file, include_optimizer=False)

Baseline test accuracy: 0.9794999957084656
Saving model to:  /tmpfs/tmp/tmp4jtqm344.h5


/tmpfs/tmp/ipykernel_35128/3680774635.py:8: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native TF-Keras format, e.g. `model.save('my_model.keras')`.
  keras.models.save_model(model, keras_file, include_optimizer=False)


## Cluster and fine-tune the model with 8 clusters

Apply the `cluster_weights()` API to cluster the whole pre-trained model to demonstrate and observe its effectiveness in reducing the model size when applying zip, while maintaining accuracy. For how best to use the API to achieve the best compression rate while maintaining your target accuracy, refer to the [clustering comprehensive guide](https://www.tensorflow.org/model_optimization/guide/clustering/clustering_comprehensive_guide).

### Define the model and apply the clustering API

The model needs to be pre-trained before using the clustering API.

In [6]:
import tensorflow_model_optimization as tfmot

cluster_weights = tfmot.clustering.keras.cluster_weights
CentroidInitialization = tfmot.clustering.keras.CentroidInitialization

clustering_params = {
  'number_of_clusters': 8,
  'cluster_centroids_init': CentroidInitialization.KMEANS_PLUS_PLUS,
  'cluster_per_channel': True,
}

clustered_model = cluster_weights(model, **clustering_params)

# Use smaller learning rate for fine-tuning
opt = keras.optimizers.Adam(learning_rate=1e-5)

clustered_model.compile(
  loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
  optimizer=opt,
  metrics=['accuracy'])

clustered_model.summary()

Model: "sequential"


_________________________________________________________________


 Layer (type)                Output Shape              Param #   


 cluster_reshape (ClusterWe  (None, 28, 28, 1)         0         


 ights)                                                          


...

 hts)                                                            


Total params: 40902 (239.41 KB)


Trainable params: 20514 (80.13 KB)


Non-trainable params: 20388 (159.28 KB)


_________________________________________________________________


### Fine-tune the model and evaluate the accuracy against baseline

Fine-tune the model with clustering for 3 epochs.

In [7]:
# Fine-tune model
clustered_model.fit(
  train_images,
  train_labels,
  epochs=3,
  validation_split=0.1)

Epoch 1/3


   1/1688 [..............................] - ETA: 42:38 - loss: 0.0101 - accuracy: 1.0000

  11/1688 [..............................] - ETA: 8s - loss: 0.0176 - accuracy: 0.9943   

  21/1688 [..............................] - ETA: 8s - loss: 0.0414 - accuracy: 0.9881

  32/1688 [..............................] - ETA: 8s - loss: 0.0406 - accuracy: 0.9883

...

1651/1688 [============================>.] - ETA: 0s - loss: 0.0328 - accuracy: 0.9908

1662/1688 [============================>.] - ETA: 0s - loss: 0.0327 - accuracy: 0.9908

1673/1688 [============================>.] - ETA: 0s - loss: 0.0327 - accuracy: 0.9908

1684/1688 [============================>.] - ETA: 0s - loss: 0.0327 - accuracy: 0.9908

1688/1688 [==============================] - 8s 5ms/step - loss: 0.0328 - accuracy: 0.9908 - val_loss: 0.0518 - val_accuracy: 0.9853


Define helper functions to calculate and print the number of clustering in each kernel of the model.

In [8]:
def print_model_weight_clusters(model):

    for layer in model.layers:
        if isinstance(layer, keras.layers.Wrapper):
            weights = layer.trainable_weights
        else:
            weights = layer.weights
        for weight in weights:
            # ignore auxiliary quantization weights
            if "quantize_layer" in weight.name:
                continue
            if "kernel" in weight.name:
                unique_count = len(np.unique(weight))
                print(
                    f"{layer.name}/{weight.name}: {unique_count} clusters "
                )

Check that the model kernels were correctly clustered. We need to strip the clustering wrapper first.

In [9]:
stripped_clustered_model = tfmot.clustering.keras.strip_clustering(clustered_model)

print_model_weight_clusters(stripped_clustered_model)

conv2d/kernel:0: 96 clusters 
dense/kernel:0: 8 clusters 


For this example, there is minimal loss in test accuracy after clustering, compared to the baseline.

In [10]:
_, clustered_model_accuracy = clustered_model.evaluate(
  test_images, test_labels, verbose=0)

print('Baseline test accuracy:', baseline_model_accuracy)
print('Clustered test accuracy:', clustered_model_accuracy)

Baseline test accuracy: 0.9794999957084656
Clustered test accuracy: 0.9804999828338623


## Apply QAT and CQAT and check effect on model clusters in both cases

Next, we apply both QAT and cluster preserving QAT (CQAT) on the clustered model and observe that CQAT preserves weight clusters in your clustered model. Note that we stripped clustering wrappers from your model with `tfmot.clustering.keras.strip_clustering` before applying CQAT API.

In [11]:
# QAT
qat_model = tfmot.quantization.keras.quantize_model(stripped_clustered_model)

qat_model.compile(optimizer='adam',
              loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])
print('Train qat model:')
qat_model.fit(train_images, train_labels, batch_size=128, epochs=1, validation_split=0.1)

# CQAT
quant_aware_annotate_model = tfmot.quantization.keras.quantize_annotate_model(
              stripped_clustered_model)
cqat_model = tfmot.quantization.keras.quantize_apply(
              quant_aware_annotate_model,
              tfmot.experimental.combine.Default8BitClusterPreserveQuantizeScheme())

cqat_model.compile(optimizer='adam',
              loss=keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])
print('Train cqat model:')
cqat_model.fit(train_images, train_labels, batch_size=128, epochs=1, validation_split=0.1)

Train qat model:


  1/422 [..............................] - ETA: 4:03 - loss: 0.0232 - accuracy: 1.0000

  8/422 [..............................] - ETA: 3s - loss: 0.0262 - accuracy: 0.9951  

 16/422 [>.............................] - ETA: 2s - loss: 0.0326 - accuracy: 0.9917

 23/422 [>.............................] - ETA: 2s - loss: 0.0322 - accuracy: 0.9908

...

391/422 [==========================>...] - ETA: 0s - loss: 0.0316 - accuracy: 0.9906

399/422 [===========================>..] - ETA: 0s - loss: 0.0316 - accuracy: 0.9906

407/422 [===========================>..] - ETA: 0s - loss: 0.0317 - accuracy: 0.9906

415/422 [============================>.] - ETA: 0s - loss: 0.0320 - accuracy: 0.9905

422/422 [==============================] - 5s 8ms/step - loss: 0.0320 - accuracy: 0.9906 - val_loss: 0.0546 - val_accuracy: 0.9863


In [12]:
print("QAT Model clusters:")
print_model_weight_clusters(qat_model)
print("CQAT Model clusters:")
print_model_weight_clusters(cqat_model)

QAT Model clusters:
quant_conv2d/conv2d/kernel:0: 108 clusters 
quant_dense/dense/kernel:0: 19875 clusters 
CQAT Model clusters:
quant_conv2d/conv2d/kernel:0: 96 clusters 
quant_dense/dense/kernel:0: 8 clusters 


## See compression benefits of CQAT model

Define helper function to get zipped model file.

In [13]:
def get_gzipped_model_size(file):
  # It returns the size of the gzipped model in kilobytes.

  _, zipped_file = tempfile.mkstemp('.zip')
  with zipfile.ZipFile(zipped_file, 'w', compression=zipfile.ZIP_DEFLATED) as f:
    f.write(file)

  return os.path.getsize(zipped_file)/1000

Note that this is a small model. Applying clustering and CQAT to a bigger production model would yield a more significant compression.

In [14]:
# QAT model
converter = tf.lite.TFLiteConverter.from_keras_model(qat_model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
qat_tflite_model = converter.convert()
qat_model_file = 'qat_model.tflite'
# Save the model.
with open(qat_model_file, 'wb') as f:
    f.write(qat_tflite_model)
    
# CQAT model
converter = tf.lite.TFLiteConverter.from_keras_model(cqat_model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
cqat_tflite_model = converter.convert()
cqat_model_file = 'cqat_model.tflite'
# Save the model.
with open(cqat_model_file, 'wb') as f:
    f.write(cqat_tflite_model)
    
print("QAT model size: ", get_gzipped_model_size(qat_model_file), ' KB')
print("CQAT model size: ", get_gzipped_model_size(cqat_model_file), ' KB')

INFO:tensorflow:Assets written to: /tmpfs/tmp/tmp73wvj7cw/assets


INFO:tensorflow:Assets written to: /tmpfs/tmp/tmp73wvj7cw/assets


/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/lite/python/convert.py:854: UserWarning: Statistics for quantized inputs were expected, but not specified; continuing anyway.
  warnings.warn(
W0000 00:00:1750506201.635118   35128 tf_tfl_flatbuffer_helpers.cc:365] Ignored output_format.
W0000 00:00:1750506201.635158   35128 tf_tfl_flatbuffer_helpers.cc:368] Ignored drop_control_dependency.
I0000 00:00:1750506201.653463   35128 mlir_graph_optimization_pass.cc:425] MLIR V1 optimization pass is not enabled


INFO:tensorflow:Assets written to: /tmpfs/tmp/tmpv94mht_r/assets


INFO:tensorflow:Assets written to: /tmpfs/tmp/tmpv94mht_r/assets


QAT model size:  18.36  KB
CQAT model size:  10.974  KB


/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/lite/python/convert.py:854: UserWarning: Statistics for quantized inputs were expected, but not specified; continuing anyway.
  warnings.warn(
W0000 00:00:1750506203.935681   35128 tf_tfl_flatbuffer_helpers.cc:365] Ignored output_format.
W0000 00:00:1750506203.935712   35128 tf_tfl_flatbuffer_helpers.cc:368] Ignored drop_control_dependency.


## See the persistence of accuracy from TF to TFLite

Define a helper function to evaluate the TFLite model on the test dataset.

In [15]:
def eval_model(interpreter):
  input_index = interpreter.get_input_details()[0]["index"]
  output_index = interpreter.get_output_details()[0]["index"]

  # Run predictions on every image in the "test" dataset.
  prediction_digits = []
  for i, test_image in enumerate(test_images):
    if i % 1000 == 0:
      print(f"Evaluated on {i} results so far.")
    # Pre-processing: add batch dimension and convert to float32 to match with
    # the model's input data format.
    test_image = np.expand_dims(test_image, axis=0).astype(np.float32)
    interpreter.set_tensor(input_index, test_image)

    # Run inference.
    interpreter.invoke()

    # Post-processing: remove batch dimension and find the digit with highest
    # probability.
    output = interpreter.tensor(output_index)
    digit = np.argmax(output()[0])
    prediction_digits.append(digit)

  print('\n')
  # Compare prediction results with ground truth labels to calculate accuracy.
  prediction_digits = np.array(prediction_digits)
  accuracy = (prediction_digits == test_labels).mean()
  return accuracy

You evaluate the model, which has been clustered and quantized, and then see the accuracy from TensorFlow persists in the TFLite backend.

In [16]:
interpreter = tf.lite.Interpreter(cqat_model_file)
interpreter.allocate_tensors()

cqat_test_accuracy = eval_model(interpreter)

print('Clustered and quantized TFLite test_accuracy:', cqat_test_accuracy)
print('Clustered TF test accuracy:', clustered_model_accuracy)

/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/lite/python/interpreter.py:457: UserWarning:     Warning: tf.lite.Interpreter is deprecated and is scheduled for deletion in
    TF 2.20. Please use the LiteRT interpreter from the ai_edge_litert package.
    See the [migration guide](https://ai.google.dev/edge/litert/migration)
    for details.
    
  warnings.warn(_INTERPRETER_DELETION_WARNING)
INFO: Created TensorFlow Lite XNNPACK delegate for CPU.


Evaluated on 0 results so far.
Evaluated on 1000 results so far.
Evaluated on 2000 results so far.
Evaluated on 3000 results so far.


Evaluated on 4000 results so far.
Evaluated on 5000 results so far.
Evaluated on 6000 results so far.
Evaluated on 7000 results so far.


Evaluated on 8000 results so far.
Evaluated on 9000 results so far.


Clustered and quantized TFLite test_accuracy: 0.9807
Clustered TF test accuracy: 0.9804999828338623


## Apply post-training quantization and compare to CQAT model

Next, we use post-training quantization (no fine-tuning) on the clustered model and check its accuracy against the CQAT model. This demonstrates why you would need to use CQAT to improve the quantized model's accuracy. The difference may not be very visible, because the MNIST model is quite small and overparametrized.

First, define a generator for the callibration dataset from the first 1000 training images.

In [17]:
def mnist_representative_data_gen():
  for image in train_images[:1000]:  
    image = np.expand_dims(image, axis=0).astype(np.float32)
    yield [image]

Quantize the model and compare accuracy to the previously acquired CQAT model. Note that the model quantized with fine-tuning achieves higher accuracy.

In [18]:
converter = tf.lite.TFLiteConverter.from_keras_model(stripped_clustered_model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
converter.representative_dataset = mnist_representative_data_gen
post_training_tflite_model = converter.convert()
post_training_model_file = 'post_training_model.tflite'
# Save the model.
with open(post_training_model_file, 'wb') as f:
    f.write(post_training_tflite_model)
    
# Compare accuracy
interpreter = tf.lite.Interpreter(post_training_model_file)
interpreter.allocate_tensors()

post_training_test_accuracy = eval_model(interpreter)

print('CQAT TFLite test_accuracy:', cqat_test_accuracy)
print('Post-training (no fine-tuning) TF test accuracy:', post_training_test_accuracy)

INFO:tensorflow:Assets written to: /tmpfs/tmp/tmpie84g8hn/assets


INFO:tensorflow:Assets written to: /tmpfs/tmp/tmpie84g8hn/assets


/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/lite/python/convert.py:854: UserWarning: Statistics for quantized inputs were expected, but not specified; continuing anyway.
  warnings.warn(


W0000 00:00:1750506205.617908   35128 tf_tfl_flatbuffer_helpers.cc:365] Ignored output_format.
W0000 00:00:1750506205.617940   35128 tf_tfl_flatbuffer_helpers.cc:368] Ignored drop_control_dependency.
fully_quantize: 0, inference_type: 6, input_inference_type: FLOAT32, output_inference_type: FLOAT32
/tmpfs/src/tf_docs_env/lib/python3.9/site-packages/tensorflow/lite/python/interpreter.py:457: UserWarning:     Warning: tf.lite.Interpreter is deprecated and is scheduled for deletion in
    TF 2.20. Please use the LiteRT interpreter from the ai_edge_litert package.
    See the [migration guide](https://ai.google.dev/edge/litert/migration)
    for details.
    
  warnings.warn(_INTERPRETER_DELETION_WARNING)


Evaluated on 0 results so far.
Evaluated on 1000 results so far.
Evaluated on 2000 results so far.
Evaluated on 3000 results so far.


Evaluated on 4000 results so far.
Evaluated on 5000 results so far.
Evaluated on 6000 results so far.
Evaluated on 7000 results so far.


Evaluated on 8000 results so far.
Evaluated on 9000 results so far.


CQAT TFLite test_accuracy: 0.9807
Post-training (no fine-tuning) TF test accuracy: 0.9799


## Conclusion

In this tutorial, you learned how to create a model, cluster it using the `cluster_weights()` API, and apply the cluster preserving quantization aware training (CQAT) to preserve clusters while using QAT. The final CQAT model was compared to the QAT one to show that the clusters are preserved in the former and lost in the latter. Next, the models were converted to TFLite to show the compression benefits of chaining clustering and CQAT model optimization techniques and the TFLite model was evaluated to ensure that the accuracy persists in the TFLite backend. Finally, the CQAT model was compared to a quantized clustered model achieved using the post-training quantization API to demonstrate the advantage of CQAT in recovering the accuracy loss from normal quantization.